# Project PM IF14 - Kelompok 11

TASK 
1. Download data pada https://drive.google.com/uc?id=1GWmtUYPa39fvpvCdAtZCY87-wuGUgC8L
2. Buka data tersebut menggunakan sqlite, kemudian disana terdapat table t_comment
3. Pada field comment, terdapat beberapa kalimat yang penulisannya tidak sesuai dengan KBBI
4. Lakukan tokenizing dll kemudian gunakan algoritma Machine learning yang dianggap cocok oleh
kelompok anda untuk memperbaiki kata pada kalimat-kalimat tersebut secara otomatis, missal:
Kmrn seharusnya menjadi kemarin
yg seharusnya menjadi yang
dmn seharusnya menjadi dimana
Anda bebas menggunakan pendekatan algoritma apa saja termasuk diluar algoritma yang anda
pelajari sebelumnya

- Data

In [1]:
#Library
import sqlite3 as sql
import warnings
warnings.filterwarnings("ignore")                     #Ignoring unnecessory warnings

import numpy as np                                  #for large and multi-dimensional arrays
import pandas as pd                                 #for data manipulation and analysis
import nltk                                         #Natural language processing tool-kit

In [2]:
#Import Database
con = sql.connect("C:/Users/hp/Praktikum ML/Project ML/DBnews.db")
dataset = pd.read_sql_query("SELECT comment FROM t_comments", con)
dataset

comment
0       WKWKWK, GAK SEKALIAN PAK, SELAWAT KE DPR... KA...
1       Mantab.. ini br dakwah yg sejati.. kl d tempat...
2                                   Salut buat Gus Miftah
3       yg nyinyir gak pernah lihat dan baca atw menge...
4       Ada adabnya sholawat. Lebih baik ajak ke majel...
...                                                   ...
598092  212 nggak pernah ngadain acara beginian ya.......
598093           TBG... Sayank.. salah pilih kendraaan..�
598094                     Saya bersama TGB pilih Jokowi�
598095  Hijrah dari hoax ke non hoax, dari ngawur ke b...
598096                     MAJU TERUS 01 !!! %uD83D%uDC4D

[598097 rows x 1 columns]

- Case Folding

In [3]:
# ------ Case Folding --------
# gunakan fungsi Series.str.lower() pada Pandas
dataset['comment'] = dataset['comment'].str.lower()


print('Case Folding Result : \n')
print(dataset['comment'].head(5))
print('\n\n\n')

Case Folding Result : 

0    wkwkwk, gak sekalian pak, selawat ke dpr... ka...
1    mantab.. ini br dakwah yg sejati.. kl d tempat...
2                                salut buat gus miftah
3    yg nyinyir gak pernah lihat dan baca atw menge...
4    ada adabnya sholawat. lebih baik ajak ke majel...
Name: comment, dtype: object






- Cleaning Data 

In [4]:
import re 
parse = re.compile('[^a-zA-Z]+')
dataset['comment'] = [parse.sub(' ', x) for x in dataset['comment'].tolist()]

print('Cleaning Data : \n') 
print(dataset['comment'].head())
print('\n\n\n')

Cleaning Data : 

0    wkwkwk gak sekalian pak selawat ke dpr kan ban...
1    mantab ini br dakwah yg sejati kl d tempat umu...
2                                salut buat gus miftah
3    yg nyinyir gak pernah lihat dan baca atw menge...
4    ada adabnya sholawat lebih baik ajak ke majeli...
Name: comment, dtype: object






- Tokenization with NLTK

In [5]:
# import word_tokenize & FreqDist from NLTK
from nltk.tokenize import word_tokenize 
from nltk.probability import FreqDist

# NLTK word tokenize 
def word_tokenize_wrapper(text):
    return word_tokenize(text)

dataset['comment'] = dataset['comment'].apply(word_tokenize_wrapper)

print('Tokenizing Result : \n') 
print(dataset['comment'].head())
print('\n\n\n')

Tokenizing Result : 

0    [wkwkwk, gak, sekalian, pak, selawat, ke, dpr,...
1    [mantab, ini, br, dakwah, yg, sejati, kl, d, t...
2                           [salut, buat, gus, miftah]
3    [yg, nyinyir, gak, pernah, lihat, dan, baca, a...
4    [ada, adabnya, sholawat, lebih, baik, ajak, ke...
Name: comment, dtype: object






- Frequency Distribution

In [6]:
# NLTK calc frequency distribution
def freqDist_wrapper(text):
    return FreqDist(text)

dataset['comment_fdist'] = dataset['comment'].apply(freqDist_wrapper)

print('Frequency Tokens : \n') 
print(dataset['comment_fdist'].head().apply(lambda x : x.most_common()))
print('\n\n\n')

Frequency Tokens : 

0    [(wkwkwk, 1), (gak, 1), (sekalian, 1), (pak, 1...
1    [(ini, 2), (biasa, 2), (mantab, 1), (br, 1), (...
2       [(salut, 1), (buat, 1), (gus, 1), (miftah, 1)]
3    [(yg, 2), (dan, 2), (cara, 2), (dg, 2), (nyiny...
4    [(ada, 1), (adabnya, 1), (sholawat, 1), (lebih...
Name: comment_fdist, dtype: object






- Normalization

In [7]:
#Normalisasi 
normalizad_word = pd.read_csv("C:/Users/hp/Praktikum ML/Project ML/kamus_alay.csv")

normalizad_word_dict = {}

for index, row in normalizad_word.iterrows():
    if row[0] not in normalizad_word_dict:
        normalizad_word_dict[row[0]] = row[1] 

def normalized_term(document):
    return [normalizad_word_dict[term] if term in normalizad_word_dict else term for term in document]

dataset['comment_normalized'] = dataset['comment'].apply(normalized_term)

dataset['comment_normalized'].head(10)

0    [wkwkwk, enggak, sekalian, pak, selawat, ke, d...
1    [mantab, ini, baru, dakwah, yang, sejati, kala...
2                           [salut, buat, gus, miftah]
3    [yang, nyinyir, enggak, pernah, lihat, dan, ba...
4    [ada, adabnya, sholawat, lebih, baik, ajak, ke...
5    [setiap, ulama, punya, jalan, dan, cara, dakwa...
6                              [umpanin, nocannya, ya]
7                  [itulah, ceramah, yang, sebenarnya]
8                        [besok, bugil, saja, selawat]
9    [bedanya, gus, miftah, dengan, fpi, hti, bagai...
Name: comment_normalized, dtype: object

- Filtering (Stopword Removal)

In [8]:
from nltk.corpus import stopwords

# get stopword indonesia
list_stopwords = stopwords.words('indonesian')

# # append additional stopword
# list_stopwords.extend(["yg", "dg", "rt", "dgn", "ny", "d", 'klo', 
#                        'kalo', 'amp', 'biar', 'bikin', 'bilang', 
#                        'gak', 'ga', 'krn', 'nya', 'nih', 'sih', 
#                        'si', 'tau', 'tdk', 'tuh', 'utk', 'ya', 
#                        'jd', 'jgn', 'sdh', 'aja', 'ya', 'n', 't', 
#                        'nyg', 'hehe', 'pen', 'u', 'nan', 'loh', 'rt','wkwkwk','prabocor','lol',
#                        'swt', 'az', 'bahahahaaaaaaaaaaaa','an','deh','mah','jqn','ez','kumkmp'])

list_stopwords = set(list_stopwords)
# list_stopwords 

In [9]:
#remove stopword pada list token
def stopwords_removal(words):
    return [word for word in words if not word in list_stopwords]

dataset['comment_WSW'] = dataset['comment_normalized'].apply(stopwords_removal) 


print(dataset['comment_WSW'].head())

0             [wkwkwk, selawat, dpr, koruptor, disana]
1                   [mantab, dakwah, sejati, mah, deh]
2                                 [salut, gus, miftah]
3    [nyinyir, lihat, baca, sejarah, dakwah, waliso...
4             [adabnya, sholawat, ajak, majelis, ilmu]
Name: comment_WSW, dtype: object


- Result wirh Sastrawi

In [10]:
# import Sastrawi package
from Sastrawi.Stemmer.StemmerFactory import StemmerFactory
import swifter


# create stemmer
factory = StemmerFactory()
stemmer = factory.create_stemmer()

# stemmed
def stemmed_wrapper(term):
    return stemmer.stem(term)

term_dict = {}

for document in dataset['comment_WSW']:
    for term in document:
        if term not in term_dict:
            term_dict[term] = ' '
            
print(len(term_dict))
print("------------------------")

for term in term_dict:
    term_dict[term] = stemmed_wrapper(term)
    print(term,":" ,term_dict[term])
    
print(term_dict)
print("------------------------")


# apply stemmed term to dataframe
def get_stemmed_term(document):
    return [term_dict[term] for term in document]

dataset['comment_stemmed'] = dataset['comment_WSW'].swifter.apply(get_stemmed_term)
print(dataset['comment_stemmed'])

164430
------------------------
wkwkwk : wkwkwk
selawat : selawat
dpr : dpr
koruptor : koruptor
disana : sana
mantab : mantab
dakwah : dakwah
sejati : sejati
mah : mah
deh : deh
salut : salut
gus : gus
miftah : miftah
nyinyir : nyinyir
lihat : lihat
baca : baca
sejarah : sejarah
walisongo : walisongo
sunan : sunan
kali : kali
jaga : jaga
kebaikan : baik
ajk : ajk
berzina : zina
lakukan : laku
porsi : porsi
sikon : sikon
adabnya : adab
sholawat : sholawat
ajak : ajak
majelis : majelis
ilmu : ilmu
ulama : ulama
jalan : jalan
kemunkaran : kemunkaran
lawan : lawan
tanganmu : tangan
kekuatanmu : kuat
mulutmu : mulut
hatimu : hati
selemah : lemah
lemahnya : lemah
iman : iman
kewajiban : wajib
kalo : kalo
komen : komen
otaknya : otak
disisipin : disisipin
politik : politik
umpanin : umpanin
nocannya : nocannya
ya : ya
ceramah : ceramah
besok : besok
bugil : bugil
bedanya : beda
fpi : fpi
hti : hti
surga : surga
neraka : neraka
penuh : penuh
kasih : kasih
penghancuran : hancur
kerjanya : kerja

penerbitan : terbit
dirundingkan : runding
ditawari : tawar
memblokade : blokade
pengurus : urus
diperbolehkan : boleh
perda : perda
membangun : bangun
merugikan : rugi
dinas : dinas
pengawasan : awas
bertindak : tindak
masuuukkk : masuuukkk
pakk : pakk
pastinya : pasti
bermasalah : masalah
ngeblokade : ngeblokade
ditutup : tutup
dikasih : kasih
ketok : ketok
cmasuk : cmasuk
blokade : blokade
musyawarahkan : musyawarah
setega : tega
jlan : jlan
waras : waras
tenang : tenang
gusti : gusti
sare : sare
diselesaikan : selesai
dilempar : lempar
memangnya : memang
koran : koran
lempar : lempar
dititipkan : titip
suratnya : surat
paspampres : paspampres
dikejar : kejar
pampapres : pampapres
ngelempar : ngelempar
benda : benda
tugas : tugas
menjaga : jaga
sifatmu : sifat
pikir : pikir
instropeksi : instropeksi
telinga : telinga
dibuatin : dibuatin
flyover : flyover
bandung : bandung
jabar : jabar
gubernur : gubernur
parah : parah
lapor : lapor
beresin : resin
kalees : kalees
kuat : kuat
nyeles

pidanakan : pidana
pasal : pasal
kuh : kuh
perdata : perdata
timbul : timbul
pilkada : pilkada
calon : calon
lomba : lomba
nolong : nolong
hampuraaa : hampuraaa
kejadiannya : jadi
pengertian : erti
syarat : syarat
ketentuan : tentu
tamah : tamah
dibabat : babat
matinya : mati
dterima : dterima
bumi : bumi
tuntut : tuntut
keberadaan : ada
pemiliki : milik
pencurian : curi
kebanyakan : banyak
pasrah : pasrah
mengalami : alami
persis : persis
alami : alami
alhamdullih : alhamdullih
semangat : semangat
layak : layak
belagu : belagu
musti : musti
sejahat : jahat
mendiamkan : diam
bantuin : bantuin
hmmm : hmmm
daerahnya : daerah
modus : modus
maaalah : maaalah
win : win
solution : solution
hilangnya : hilang
gerakan : gera
coin : coin
aturannya : atur
tempuh : tempuh
berusaha : usaha
nyogok : nyogok
hakim : hakim
putus : putus
asa : asa
dukungan : dukung
gunting : gunting
mengeluarkan : keluar
pp : pp
ngawasin : ngawasin
mustinya : mustinya
robohkan : roboh
halangi : halang
balikin : balikin

selimut : selimut
pikirkan : pikir
aplg : aplg
kemampuan : mampu
memimpin : pimpin
mimpi : mimpi
fiktif : fiktif
arief : arief
dibohongi : bohong
ambisi : ambisi
tenaga : tenaga
chicken : chicken
gantiketuaumumpd : gantiketuaumumpd
kuasai : kuasa
ketuan : ketu
team : team
pemilih : pilih
menerus : terus
langkah : langkah
kenyataannya : nyata
dibawah : bawah
kendali : kendali
kontrol : kontrol
cawapresnya : cawapresnya
tunduk : tunduk
bisanya : bisa
pertanggung : tanggung
sembunyi : sembunyi
tipe : tipe
petarung : tarung
nyiyir : nyiyir
penghianat : penghianat
dibiarkan : biar
elektabilitas : elektabilitas
ngangkat : ngangkat
joss : joss
prediksi : prediksi
realita : realita
drps : drps
hua : hua
ha : ha
cemas : cemas
parlemen : parlemen
colapsnya : colapsnya
ndi : ndi
jongosnya : jongos
obyektif : obyektif
elektoral : elektoral
tergerus : gerus
proporsi : proporsi
berbicara : bicara
ratapan : ratap
kopong : kopong
menunjukan : tunjuk
kepeminpinan : kepeminpinan
gembosin : gembosin
seni

hahahahahaha : hahahahahaha
diselah : lah
hancurrrrrr : hancurrrrrr
didepak : depak
maklum : maklum
pedagang : dagang
jualan : jual
pusinggggg : pusinggggg
berteman : teman
pilihannya : pilih
buntung : buntung
ucapanya : ucapanya
kecilnya : kecil
meraup : raup
persiapan : siap
ketinggalan : tinggal
memprediksi : prediksi
pasi : pasi
riak : riak
gelombang : gelombang
plun : plun
gampangnya : gampang
rugilah : rugi
royal : royal
kebingungan : bingung
ajag : ajag
ijik : ijik
kemarih : kemarih
yekan : yekan
nyiapin : nyiapin
hahahahahhaahhahahahahahaha : hahahahahhaahhahahahahahaha
prettttt : prettttt
ditinggal : tinggal
grass : grass
root : root
mengakui : aku
dasarnya : dasar
sokan : sok
shame : shame
you : you
mami : mami
jaginya : jaginya
gender : gender
berkarier : karier
digunting : gunting
bersiaplah : siap
setimpal : timpal
ketegasan : tegas
selevel : level
prabowogakjadipresiden : prabowogakjadipresiden
kemudi : kemudi
keburu : keburu
kiloan : kilo
luwes : luwes
case : case
jomin 

...

sulardi : sulardi
gogah : gogah
ngeni : ngeni
belaaa : belaaa
intorpeksi : intorpeksi
aaawww : aaawww
aaaaw : aaaaw
aaaww : aaaww
berbusuk : busuk
mikirrrrrrrrrrr : mikirrrrrrrrrrr
diskrikan : diskrikan
dikakukan : kaku
dijdin : dijdin
telatt : telatt
kesetianya : setia
sarungpeait : sarungpeait
dipeecaya : dipeecaya
dinaikinnya : dinaikinnya
kesetia : setia
dannpendukung : dannpendukung
misuuuuui : misuuuuui
bejan : bejan
databgi : databgi
ysaha : ysaha
keluarjan : keluarjan
smasa : smasa
ttapkan : ttapkan
kambamgan : kambamgan
bloommm : bloommm
seremmmmmm : seremmmmmm
blombongan : blombongan
finallllyyyyyyy : finallllyyyyyyy
aiap : aiap
surveyny : surveyny
menyurvey : menyurvey
velas : vas
intenal : intenal
serveyor : serveyor
srinarendra : srinarendra
oponeeeeeeee : oponeeeeeeee
qiqiqiqiqiqiqiqiqiqi : qiqiqiqiqiqiqiqiqiqi
ngindonesiamaju : ngindonesiamaju
jolie : jolie
singnge : singnge
iupahsampeyanikisopo : iupahsampeyanikisopo
dilspangan : dilspangan
unfair : unfair
blnan : blnan

nggedabrussss : nggedabrussss
hemna : hemna
nggilaniiiiiiiiii : nggilaniiiiiiiiii
terselimuti : limut
menyusulnya : susul
tanapa : tanapa
pinsip : pinsip
savedewa : savedewa
riphatespeech : riphatespeech
dipindahnya : pindah
dengi : dengi
kebangs : kebangs
wkwkwwkkwkwkwk : wkwkwwkkwkwkwk
tukus : tukus
muampyuuuusssss : muampyuuuusssss
pilotikus : pilotikus
dislhin : dislhin
mngulanginya : mngulanginya
beratmah : beratmah
mualess : mualess
ditundukkan : tunduk
ngrjain : ngrjain
hajardah : hajardah
nelusuri : nelusuri
banguninnya : banguninnya
ajaiiib : ajaiiib
yulia : yulia
criga : criga
mampuanya : mampuanya
bohongkah : bohong
poanas : poanas
kwkwkwwkwkkwk : kwkwkwwkwkkwk
bangethaha : bangethaha
mantaaaaaaaaapppppppppppppppppppppppppppppppp : mantaaaaaaaaapppppppppppppppppppppppppppppppp
artissss : artissss
jeulma : jeulma
benewr : benewr
sampaaaaaaaaaaaaaah : sampaaaaaaaaaaaaaah
pnjajahan : pnjajahan
djajah : djajah
digitalny : digitalny
dulubsama : dulubsama
munyuuk : munyuuk
ngaxco 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




------------------------



0                    [wkwkwk, selawat, dpr, koruptor, sana]
1                        [mantab, dakwah, sejati, mah, deh]
2                                      [salut, gus, miftah]
3         [nyinyir, lihat, baca, sejarah, dakwah, waliso...
4                     [adab, sholawat, ajak, majelis, ilmu]
                                ...                        
598092    [ada, acara, ya, program, agama, ya, kalo, ada...
598093               [tbg, sayank, salah, pilih, kendraaan]
598094                                 [tgb, pilih, jokowi]
598095    [hijrah, hoax, non, hoax, ngawur, jelek, puji,...
598096                                          [maju, udc]
Name: comment_stemmed, Length: 598097, dtype: object
